In [1]:
def prefill(board, h, v, n):
    def build(l, n):
        res = [0] * n
        presum, postsum = [0], [0]
        for _v in l:
            presum.append(presum[-1] + _v + 1)
        for _v in l[::-1]:
            postsum.append(postsum[-1] + _v + 1)
        postsum.pop()
        postsum = postsum[::-1]
        for i,_v in enumerate(l):
            low_e = presum[i] + (_v-1)
            high_s = n-1 - postsum[i] - (_v-1)
            for j in range(high_s, low_e+1):
                res[j] = _v
        return res
    for i in range(n):
        hm = build(h[i], n)
        vm = build(v[i], n)
        for j in range(n):
            board[i][j][0] = hm[j]
            board[j][i][1] = vm[j]
    return

In [2]:
def pos_lines(l, bline, o, n):
    '''
    return a list of all possible line outcomes, 
    considering l and board
    '''
    
#     build bl to represent the line
#     -1 -> cannot be mark
#     0 -> undetermined
#     n+1 -> need to be a mark
#     others -> is a mark
    bl = [0] * n
    if o == "h":
        for i in range(n):
            if bline[i][1] == 0:
                bl[i] = bline[i][0]
            elif bline[i][1] == -1:
                bl[i] = -1
            else:
                bl[i] = n+1
    else:
        for i in range(n):
            if bline[i][0] == 0:
                bl[i] = bline[i][1]
            elif bline[i][0] == -1:
                bl[i] = -1
            else:
                bl[i] = n+1
    
#     all possible lines from l
    def perm(l, n):
        def dfs(l, n, idx, ls, dres):
            sls = sum(ls)
            if sls > n:
                return
            if idx == len(l):
                dres.append(ls + [n-sls])
                return
            if idx == 0:
                for g in range(n-l[idx]+1):
                    dfs(l, n, idx+1, ls + [g, l[idx]], dres)
            else:
                for g in range(1, n-l[idx]+1-sls):
                    dfs(l, n, idx+1, ls + [g, l[idx]], dres)
            return
        def convt(l, n):
            res = [-1] * n
            i = l[0]
            ln = len(l)
            for li in range(1, ln, 2):
                for j in range(l[li]):
                    res[i+j] = l[li]
                i += (l[li] + l[li+1])
            return res
            
        dres = []
        dfs(l, n, 0, [], dres)
        res = [convt(_, n) for _ in dres]
        return res
    
#     test if possible line conflicts with bl
    def valid(l, bl, n):
        for i in range(n):
            if bl[i] == 0:
                continue
            if l[i] == -1 and bl[i] != -1:
                return False
            elif bl[i] != l[i] and bl[i] != n+1:
                return False
        return True
    
    return [_ for _ in perm(l, n) if valid(_, bl, n)]

def vvalid(board, vl, idx, n):
    def val(bl, l, idx, n):
        bi, li = 0, 0
        tl = []
        while bi <= idx:
            if bl[bi][0] != -1:
                t = 0
                while bi + t <= idx and bl[bi+t][0] != -1:
                    t += 1
                tl.append(t)
                bi += t
            else:
                bi += 1
        lt = len(tl)
        if lt > len(l):
            return False
#         print("val len t", lt, "temp list", tl, "\nboard list",
#               bl, "\ncol list", l, "\nindex", idx, "\n", "-"*10)
        for i in range(lt-1):
            if l[i] != tl[i]:
                return False
        
        if lt > 0 and l[lt-1] < tl[lt-1]:
            return False
        if idx == n-1:
            if len(l) != lt or tl[-1] != l[-1]:
                return False
        
        return True
    
    for i in range(n):
        bl = [board[j][i] for j in range(n)]
        if not val(bl, vl[i], idx, n):
            return False
    return True

import copy
def fill(board, h, v, idx, n):
    if idx == n:
        print("fill succeed!!")
        print(*board, sep= '\n')
        print("*"*15)
        return True
    possible_lines = pos_lines(h[idx], board[idx], 'h', n)
    print("in fill line {}, there are {} pls".format(idx, len(possible_lines)), possible_lines)
    if not possible_lines or len(possible_lines) == 0:
        return False
    bl_holder = copy.deepcopy(board[idx])
    for pl in possible_lines:
        for j in range(n):
            board[idx][j][0] = pl[j]
        print("trying possible lines:",idx, pl)
        print(*board, sep='\n')
        print("---"*10)
        vv = vvalid(board, v, idx, n)
        print(vv)
        if not vv:
            continue
#         if not vfill(board, lsv, idx, n):
#             continue
#         print("right after vfill:")
#         print(*board, sep='\n')
        if fill(board, h, v, idx+1, n):
            return True
    print()
    print("all trys in line {} failed".format(idx))
    print(*board, sep='\n')
    print(bl_holder)
    board[idx] = bl_holder
    print("before throw back")
    print(*board, sep='\n')
    print()
    return False

In [3]:
def solve(hlist, vlist):
    hn, vn = len(hlist), len(vlist)
    if hn != vn:
        print("Line restriction input error. Lengths not equal!")
        return
    if sum([sum(_) for _ in hlist]) != sum([sum(_) for _ in vlist]):
        print("Line restriction input error. hsum and v sum not equal!")
        return
    board = [[[0,0] for i in range(vn)] for j in range(hn)]
    prefill(board, hlist, vlist, hn)
    print("after prefill")
    print(*board, sep="\n")
    print("|"*10)
    if fill(board, hlist, vlist, 0, hn):
        print("all through")
        print(*board, sep='\n')
        print("*!"*10)
        return
    print("cannot get through")
    print(":("*10)
    print(*board, sep='\n')


In [4]:
ls_h = '''
2
4
2 1
1 3
9
7
2 4
1 4
3 1
4 3
4 1
5
1 4
7 1 2
3
'''
ls_h = [[int(i) for i in j.split(' ')] for j in ls_h.split('\n') if j]
print(len(ls_h), ls_h)
ls_v = '''
2 1
2 1
2 1
2 1
1 3 1
8 1
3 6 1
1 8
1 8
2 3 1
2 2 1
1 2
1 1 2
3 2
1 1
'''
ls_v = [[int(i) for i in j.split(' ')] for j in ls_v.split('\n') if j]
print(len(ls_v),ls_v)

15 [[2], [4], [2, 1], [1, 3], [9], [7], [2, 4], [1, 4], [3, 1], [4, 3], [4, 1], [5], [1, 4], [7, 1, 2], [3]]
15 [[2, 1], [2, 1], [2, 1], [2, 1], [1, 3, 1], [8, 1], [3, 6, 1], [1, 8], [1, 8], [2, 3, 1], [2, 2, 1], [1, 2], [1, 1, 2], [3, 2], [1, 1]]


In [5]:
%timeit solve([[1],[2],[1,1]], [[2],[1],[1,1]])

after prefill
[[0, 0], [0, 0], [0, 1]]
[[0, 2], [2, 0], [0, 0]]
[[1, 0], [0, 0], [1, 1]]
||||||||||
in fill line 0, there are 1 pls [[-1, -1, 1]]
trying possible lines: 0 [-1, -1, 1]
[[-1, 0], [-1, 0], [1, 1]]
[[0, 2], [2, 0], [0, 0]]
[[1, 0], [0, 0], [1, 1]]
------------------------------
True
in fill line 1, there are 1 pls [[2, 2, -1]]
trying possible lines: 1 [2, 2, -1]
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [0, 0], [1, 1]]
------------------------------
True
in fill line 2, there are 1 pls [[1, -1, 1]]
trying possible lines: 2 [1, -1, 1]
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [-1, 0], [1, 1]]
------------------------------
True
fill succeed!!
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [-1, 0], [1, 1]]
***************
all through
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [-1, 0], [1, 1]]
*!*!*!*!*!*!*!*!*!*!
after prefill
[[0, 0], [0, 0], [0, 1]]
[[0, 2], [2, 0], [0, 0]]
[[1, 0], [0, 0], [1, 1]]
||

in fill line 1, there are 1 pls [[2, 2, -1]]
trying possible lines: 1 [2, 2, -1]
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [0, 0], [1, 1]]
------------------------------
True
in fill line 2, there are 1 pls [[1, -1, 1]]
trying possible lines: 2 [1, -1, 1]
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [-1, 0], [1, 1]]
------------------------------
True
fill succeed!!
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [-1, 0], [1, 1]]
***************
all through
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [-1, 0], [1, 1]]
*!*!*!*!*!*!*!*!*!*!
after prefill
[[0, 0], [0, 0], [0, 1]]
[[0, 2], [2, 0], [0, 0]]
[[1, 0], [0, 0], [1, 1]]
||||||||||
in fill line 0, there are 1 pls [[-1, -1, 1]]
trying possible lines: 0 [-1, -1, 1]
[[-1, 0], [-1, 0], [1, 1]]
[[0, 2], [2, 0], [0, 0]]
[[1, 0], [0, 0], [1, 1]]
------------------------------
True
in fill line 1, there are 1 pls [[2, 2, -1]]
trying possible lines: 1 [2, 2, -1]
[[-1, 0], 

[[0, 2], [2, 0], [0, 0]]
[[1, 0], [0, 0], [1, 1]]
||||||||||
in fill line 0, there are 1 pls [[-1, -1, 1]]
trying possible lines: 0 [-1, -1, 1]
[[-1, 0], [-1, 0], [1, 1]]
[[0, 2], [2, 0], [0, 0]]
[[1, 0], [0, 0], [1, 1]]
------------------------------
True
in fill line 1, there are 1 pls [[2, 2, -1]]
trying possible lines: 1 [2, 2, -1]
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [0, 0], [1, 1]]
------------------------------
True
in fill line 2, there are 1 pls [[1, -1, 1]]
trying possible lines: 2 [1, -1, 1]
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [-1, 0], [1, 1]]
------------------------------
True
fill succeed!!
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [-1, 0], [1, 1]]
***************
all through
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [-1, 0], [1, 1]]
*!*!*!*!*!*!*!*!*!*!
after prefill
[[0, 0], [0, 0], [0, 1]]
[[0, 2], [2, 0], [0, 0]]
[[1, 0], [0, 0], [1, 1]]
||||||||||
in fill line 0, there are 1 pl

after prefill
[[0, 0], [0, 0], [0, 1]]
[[0, 2], [2, 0], [0, 0]]
[[1, 0], [0, 0], [1, 1]]
||||||||||
in fill line 0, there are 1 pls [[-1, -1, 1]]
trying possible lines: 0 [-1, -1, 1]
[[-1, 0], [-1, 0], [1, 1]]
[[0, 2], [2, 0], [0, 0]]
[[1, 0], [0, 0], [1, 1]]
------------------------------
True
in fill line 1, there are 1 pls [[2, 2, -1]]
trying possible lines: 1 [2, 2, -1]
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [0, 0], [1, 1]]
------------------------------
True
in fill line 2, there are 1 pls [[1, -1, 1]]
trying possible lines: 2 [1, -1, 1]
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [-1, 0], [1, 1]]
------------------------------
True
fill succeed!!
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [-1, 0], [1, 1]]
***************
all through
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [-1, 0], [1, 1]]
*!*!*!*!*!*!*!*!*!*!
after prefill
[[0, 0], [0, 0], [0, 1]]
[[0, 2], [2, 0], [0, 0]]
[[1, 0], [0, 0], [1, 1]]
||

trying possible lines: 0 [-1, -1, 1]
[[-1, 0], [-1, 0], [1, 1]]
[[0, 2], [2, 0], [0, 0]]
[[1, 0], [0, 0], [1, 1]]
------------------------------
True
in fill line 1, there are 1 pls [[2, 2, -1]]
trying possible lines: 1 [2, 2, -1]
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [0, 0], [1, 1]]
------------------------------
True
in fill line 2, there are 1 pls [[1, -1, 1]]
trying possible lines: 2 [1, -1, 1]
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [-1, 0], [1, 1]]
------------------------------
True
fill succeed!!
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [-1, 0], [1, 1]]
***************
all through
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [-1, 0], [1, 1]]
*!*!*!*!*!*!*!*!*!*!
after prefill
[[0, 0], [0, 0], [0, 1]]
[[0, 2], [2, 0], [0, 0]]
[[1, 0], [0, 0], [1, 1]]
||||||||||
in fill line 0, there are 1 pls [[-1, -1, 1]]
trying possible lines: 0 [-1, -1, 1]
[[-1, 0], [-1, 0], [1, 1]]
[[0, 2], [2, 0], [0, 0]]
[[

...

***************
all through
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [-1, 0], [1, 1]]
*!*!*!*!*!*!*!*!*!*!
after prefill
[[0, 0], [0, 0], [0, 1]]
[[0, 2], [2, 0], [0, 0]]
[[1, 0], [0, 0], [1, 1]]
||||||||||
in fill line 0, there are 1 pls [[-1, -1, 1]]
trying possible lines: 0 [-1, -1, 1]
[[-1, 0], [-1, 0], [1, 1]]
[[0, 2], [2, 0], [0, 0]]
[[1, 0], [0, 0], [1, 1]]
------------------------------
True
in fill line 1, there are 1 pls [[2, 2, -1]]
trying possible lines: 1 [2, 2, -1]
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [0, 0], [1, 1]]
------------------------------
True
in fill line 2, there are 1 pls [[1, -1, 1]]
trying possible lines: 2 [1, -1, 1]
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [-1, 0], [1, 1]]
------------------------------
True
fill succeed!!
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [-1, 0], [1, 1]]
***************
all through
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [

[[0, 0], [0, 0], [0, 1]]
[[0, 2], [2, 0], [0, 0]]
[[1, 0], [0, 0], [1, 1]]
||||||||||
in fill line 0, there are 1 pls [[-1, -1, 1]]
trying possible lines: 0 [-1, -1, 1]
[[-1, 0], [-1, 0], [1, 1]]
[[0, 2], [2, 0], [0, 0]]
[[1, 0], [0, 0], [1, 1]]
------------------------------
True
in fill line 1, there are 1 pls [[2, 2, -1]]
trying possible lines: 1 [2, 2, -1]
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [0, 0], [1, 1]]
------------------------------
True
in fill line 2, there are 1 pls [[1, -1, 1]]
trying possible lines: 2 [1, -1, 1]
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [-1, 0], [1, 1]]
------------------------------
True
fill succeed!!
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [-1, 0], [1, 1]]
***************
all through
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [-1, 0], [1, 1]]
*!*!*!*!*!*!*!*!*!*!
after prefill
[[0, 0], [0, 0], [0, 1]]
[[0, 2], [2, 0], [0, 0]]
[[1, 0], [0, 0], [1, 1]]
||||||||||
in fi

trying possible lines: 0 [-1, -1, 1]
[[-1, 0], [-1, 0], [1, 1]]
[[0, 2], [2, 0], [0, 0]]
[[1, 0], [0, 0], [1, 1]]
------------------------------
True
in fill line 1, there are 1 pls [[2, 2, -1]]
trying possible lines: 1 [2, 2, -1]
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [0, 0], [1, 1]]
------------------------------
True
in fill line 2, there are 1 pls [[1, -1, 1]]
trying possible lines: 2 [1, -1, 1]
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [-1, 0], [1, 1]]
------------------------------
True
fill succeed!!
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [-1, 0], [1, 1]]
***************
all through
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [-1, 0], [1, 1]]
*!*!*!*!*!*!*!*!*!*!
after prefill
[[0, 0], [0, 0], [0, 1]]
[[0, 2], [2, 0], [0, 0]]
[[1, 0], [0, 0], [1, 1]]
||||||||||
in fill line 0, there are 1 pls [[-1, -1, 1]]
trying possible lines: 0 [-1, -1, 1]
[[-1, 0], [-1, 0], [1, 1]]
[[0, 2], [2, 0], [0, 0]]
[[

[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [0, 0], [1, 1]]
------------------------------
True
in fill line 2, there are 1 pls [[1, -1, 1]]
trying possible lines: 2 [1, -1, 1]
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [-1, 0], [1, 1]]
------------------------------
True
fill succeed!!
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [-1, 0], [1, 1]]
***************
all through
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [-1, 0], [1, 1]]
*!*!*!*!*!*!*!*!*!*!
after prefill
[[0, 0], [0, 0], [0, 1]]
[[0, 2], [2, 0], [0, 0]]
[[1, 0], [0, 0], [1, 1]]
||||||||||
in fill line 0, there are 1 pls [[-1, -1, 1]]
trying possible lines: 0 [-1, -1, 1]
[[-1, 0], [-1, 0], [1, 1]]
[[0, 2], [2, 0], [0, 0]]
[[1, 0], [0, 0], [1, 1]]
------------------------------
True
in fill line 1, there are 1 pls [[2, 2, -1]]
trying possible lines: 1 [2, 2, -1]
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [0, 0], [1, 1]]
-------------

[[0, 0], [0, 0], [0, 1]]
[[0, 2], [2, 0], [0, 0]]
[[1, 0], [0, 0], [1, 1]]
||||||||||
in fill line 0, there are 1 pls [[-1, -1, 1]]
trying possible lines: 0 [-1, -1, 1]
[[-1, 0], [-1, 0], [1, 1]]
[[0, 2], [2, 0], [0, 0]]
[[1, 0], [0, 0], [1, 1]]
------------------------------
True
in fill line 1, there are 1 pls [[2, 2, -1]]
trying possible lines: 1 [2, 2, -1]
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [0, 0], [1, 1]]
------------------------------
True
in fill line 2, there are 1 pls [[1, -1, 1]]
trying possible lines: 2 [1, -1, 1]
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [-1, 0], [1, 1]]
------------------------------
True
fill succeed!!
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [-1, 0], [1, 1]]
***************
all through
[[-1, 0], [-1, 0], [1, 1]]
[[2, 2], [2, 0], [-1, 0]]
[[1, 0], [-1, 0], [1, 1]]
*!*!*!*!*!*!*!*!*!*!
after prefill
[[0, 0], [0, 0], [0, 1]]
[[0, 2], [2, 0], [0, 0]]
[[1, 0], [0, 0], [1, 1]]
||||||||||
in fi

In [6]:
%timeit solve([[1],[3],[1],[2]], [[1,1],[1,1],[2],[1]])

after prefill
[[0, 0], [0, 0], [0, 0], [0, 0]]
[[0, 0], [3, 0], [3, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]
||||||||||
in fill line 0, there are 4 pls [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
trying possible lines: 0 [1, -1, -1, -1]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[0, 0], [3, 0], [3, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]
------------------------------
True
in fill line 1, there are 2 pls [[3, 3, 3, -1], [-1, 3, 3, 3]]
trying possible lines: 1 [3, 3, 3, -1]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[3, 0], [3, 0], [3, 0], [-1, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]
------------------------------
False
trying possible lines: 1 [-1, 3, 3, 3]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [3, 0], [3, 0], [3, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]
------------------------------
True
in fill line 2, there are 4 pls [[1, -1, -1,

[[-1, 0], [3, 0], [3, 0], [3, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]
------------------------------
True
in fill line 2, there are 4 pls [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
trying possible lines: 2 [1, -1, -1, -1]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [3, 0], [3, 0], [3, 0]]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]
------------------------------
True
in fill line 3, there are 3 pls [[2, 2, -1, -1], [-1, 2, 2, -1], [-1, -1, 2, 2]]
trying possible lines: 3 [2, 2, -1, -1]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [3, 0], [3, 0], [3, 0]]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[2, 0], [2, 0], [-1, 0], [-1, 0]]
------------------------------
False
trying possible lines: 3 [-1, 2, 2, -1]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [3, 0], [3, 0], [3, 0]]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [2, 0], [2, 0], [-1, 0]]
------------------------------
False
trying possible lines: 3 [-1, 

trying possible lines: 1 [3, 3, 3, -1]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[3, 0], [3, 0], [3, 0], [-1, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]
------------------------------
False
trying possible lines: 1 [-1, 3, 3, 3]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [3, 0], [3, 0], [3, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]
------------------------------
True
in fill line 2, there are 4 pls [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
trying possible lines: 2 [1, -1, -1, -1]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [3, 0], [3, 0], [3, 0]]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]
------------------------------
True
in fill line 3, there are 3 pls [[2, 2, -1, -1], [-1, 2, 2, -1], [-1, -1, 2, 2]]
trying possible lines: 3 [2, 2, -1, -1]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [3, 0], [3, 0], [3, 0]]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[2, 0], [2, 0], [-1, 0], [-1, 0]

[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [3, 0], [3, 0], [3, 0]]
[[-1, 0], [-1, 0], [1, 0], [-1, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]
------------------------------
True
in fill line 3, there are 3 pls [[2, 2, -1, -1], [-1, 2, 2, -1], [-1, -1, 2, 2]]
trying possible lines: 3 [2, 2, -1, -1]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [3, 0], [3, 0], [3, 0]]
[[-1, 0], [-1, 0], [1, 0], [-1, 0]]
[[2, 0], [2, 0], [-1, 0], [-1, 0]]
------------------------------
True
fill succeed!!
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [3, 0], [3, 0], [3, 0]]
[[-1, 0], [-1, 0], [1, 0], [-1, 0]]
[[2, 0], [2, 0], [-1, 0], [-1, 0]]
***************
all through
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [3, 0], [3, 0], [3, 0]]
[[-1, 0], [-1, 0], [1, 0], [-1, 0]]
[[2, 0], [2, 0], [-1, 0], [-1, 0]]
*!*!*!*!*!*!*!*!*!*!
after prefill
[[0, 0], [0, 0], [0, 0], [0, 0]]
[[0, 0], [3, 0], [3, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]
||||||||||
in fill line 0, there ar

[[0, 0], [0, 0], [0, 0], [0, 0]]
------------------------------
False
trying possible lines: 2 [-1, -1, 1, -1]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [3, 0], [3, 0], [3, 0]]
[[-1, 0], [-1, 0], [1, 0], [-1, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]
------------------------------
True
in fill line 3, there are 3 pls [[2, 2, -1, -1], [-1, 2, 2, -1], [-1, -1, 2, 2]]
trying possible lines: 3 [2, 2, -1, -1]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [3, 0], [3, 0], [3, 0]]
[[-1, 0], [-1, 0], [1, 0], [-1, 0]]
[[2, 0], [2, 0], [-1, 0], [-1, 0]]
------------------------------
True
fill succeed!!
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [3, 0], [3, 0], [3, 0]]
[[-1, 0], [-1, 0], [1, 0], [-1, 0]]
[[2, 0], [2, 0], [-1, 0], [-1, 0]]
***************
all through
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [3, 0], [3, 0], [3, 0]]
[[-1, 0], [-1, 0], [1, 0], [-1, 0]]
[[2, 0], [2, 0], [-1, 0], [-1, 0]]
*!*!*!*!*!*!*!*!*!*!
after prefill
[[0, 0], [0, 0], [0, 0], [0, 0]]
[[0, 0], [3, 0], [3, 0]

...

False
trying possible lines: 3 [-1, -1, 2, 2]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [3, 0], [3, 0], [3, 0]]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [-1, 0], [2, 0], [2, 0]]
------------------------------
False

all trys in line 3 failed
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [3, 0], [3, 0], [3, 0]]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [-1, 0], [2, 0], [2, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]
before throw back
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [3, 0], [3, 0], [3, 0]]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]

trying possible lines: 2 [-1, 1, -1, -1]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [3, 0], [3, 0], [3, 0]]
[[-1, 0], [1, 0], [-1, 0], [-1, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]
------------------------------
False
trying possible lines: 2 [-1, -1, 1, -1]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [3, 0], [3, 0], [3, 0]]
[[-1, 0], [-1, 0], [1, 0], [-1, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]
--------------------

trying possible lines: 2 [1, -1, -1, -1]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [3, 0], [3, 0], [3, 0]]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]
------------------------------
True
in fill line 3, there are 3 pls [[2, 2, -1, -1], [-1, 2, 2, -1], [-1, -1, 2, 2]]
trying possible lines: 3 [2, 2, -1, -1]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [3, 0], [3, 0], [3, 0]]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[2, 0], [2, 0], [-1, 0], [-1, 0]]
------------------------------
False
trying possible lines: 3 [-1, 2, 2, -1]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [3, 0], [3, 0], [3, 0]]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [2, 0], [2, 0], [-1, 0]]
------------------------------
False
trying possible lines: 3 [-1, -1, 2, 2]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [3, 0], [3, 0], [3, 0]]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [-1, 0], [2, 0], [2, 0]]
------------------------------
False

all trys in line 3 failed
[[1, 0], [-1, 0], [-1,

[[-1, 0], [2, 0], [2, 0], [-1, 0]]
------------------------------
False
trying possible lines: 3 [-1, -1, 2, 2]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [3, 0], [3, 0], [3, 0]]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [-1, 0], [2, 0], [2, 0]]
------------------------------
False

all trys in line 3 failed
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [3, 0], [3, 0], [3, 0]]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [-1, 0], [2, 0], [2, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]
before throw back
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [3, 0], [3, 0], [3, 0]]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]

trying possible lines: 2 [-1, 1, -1, -1]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [3, 0], [3, 0], [3, 0]]
[[-1, 0], [1, 0], [-1, 0], [-1, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]
------------------------------
False
trying possible lines: 2 [-1, -1, 1, -1]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [3, 0], [3, 0], [3, 0]]
[[-1, 0], [-1, 0], [1, 


trying possible lines: 2 [-1, 1, -1, -1]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [3, 0], [3, 0], [3, 0]]
[[-1, 0], [1, 0], [-1, 0], [-1, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]
------------------------------
False
trying possible lines: 2 [-1, -1, 1, -1]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [3, 0], [3, 0], [3, 0]]
[[-1, 0], [-1, 0], [1, 0], [-1, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]
------------------------------
True
in fill line 3, there are 3 pls [[2, 2, -1, -1], [-1, 2, 2, -1], [-1, -1, 2, 2]]
trying possible lines: 3 [2, 2, -1, -1]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [3, 0], [3, 0], [3, 0]]
[[-1, 0], [-1, 0], [1, 0], [-1, 0]]
[[2, 0], [2, 0], [-1, 0], [-1, 0]]
------------------------------
True
fill succeed!!
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [3, 0], [3, 0], [3, 0]]
[[-1, 0], [-1, 0], [1, 0], [-1, 0]]
[[2, 0], [2, 0], [-1, 0], [-1, 0]]
***************
all through
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [3, 0], [3, 0], [3, 0]]
[[-1, 0], [-1,

[[0, 0], [3, 0], [3, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]
||||||||||
in fill line 0, there are 4 pls [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1, -1, 1]]
trying possible lines: 0 [1, -1, -1, -1]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[0, 0], [3, 0], [3, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]
------------------------------
True
in fill line 1, there are 2 pls [[3, 3, 3, -1], [-1, 3, 3, 3]]
trying possible lines: 1 [3, 3, 3, -1]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[3, 0], [3, 0], [3, 0], [-1, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]
------------------------------
False
trying possible lines: 1 [-1, 3, 3, 3]
[[1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [3, 0], [3, 0], [3, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0]]
------------------------------
True
in fill line 2, there are 4 pls [[1, -1, -1, -1], [-1, 1, -1, -1], [-1, -1, 1, -1], [-1, -1

In [7]:
%timeit solve([[1,2],[1,2],[1,2],[2],[3],[2,1],[2,1],[1,1]],[[3,2],[2],[2],[2],[6],[2],[2],[1]])

after prefill
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0]]
[[0, 3], [0, 0], [0, 0], [0, 0], [0, 6], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 6], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 6], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 6], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0]]
||||||||||
in fill line 0, there are 15 pls [[1, -1, 2, 2, -1, -1, -1, -1], [1, -1, -1, 2, 2, -1, -1, -1], [1, -1, -1, -1, 2, 2, -1, -1], [1, -1, -1, -1, -1, 2, 2, -1], [1, -1, -1, -1, -1, -1, 2, 2], [-1, 1, -1, 2, 2, -1, -1, -1], [-1, 1, -1, -1, 2, 2, -1, -1], [-1, 1, -1, -1, -1, 2, 2, -1], [-1, 1, -1, -1, -1, -1, 2, 2], [-1, -1, 1, -1, 2, 2, -1, -1], [-1, -1, 1, -1, -1, 2, 2, -1], [-1, -1, 1, -1, -1, -1, 2, 2], [-1, -1, -1, 1, -1, 2, 2, -1], [-1, -1, -1, 1, -1

True
in fill line 2, there are 2 pls [[1, -1, -1, 2, 2, -1, -1, -1], [1, -1, -1, -1, 2, 2, -1, -1]]
trying possible lines: 2 [1, -1, -1, 2, 2, -1, -1, -1]
[[1, 0], [-1, 0], [2, 0], [2, 0], [-1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[1, 0], [-1, 0], [-1, 0], [-1, 0], [-1, 0], [2, 0], [2, 0], [-1, 0]]
[[1, 3], [-1, 0], [-1, 0], [2, 0], [2, 6], [-1, 0], [-1, 0], [-1, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 6], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 6], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 6], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0]]
------------------------------
False
trying possible lines: 2 [1, -1, -1, -1, 2, 2, -1, -1]
[[1, 0], [-1, 0], [2, 0], [2, 0], [-1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[1, 0], [-1, 0], [-1, 0], [-1, 0], [-1, 0], [2, 0], [2, 0], [-1, 0]]
[[1, 3], [-1, 0], [-1, 0], [-1, 0], [2, 6], [2, 0], [-1, 0], [-1, 0]]
[[0, 0],

trying possible lines: 2 [1, -1, -1, 2, 2, -1, -1, -1]
[[1, 0], [-1, 0], [2, 0], [2, 0], [-1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [1, 0], [-1, 0], [-1, 0], [-1, 0], [2, 0], [2, 0], [-1, 0]]
[[1, 3], [-1, 0], [-1, 0], [2, 0], [2, 6], [-1, 0], [-1, 0], [-1, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 6], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 6], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 6], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0]]
------------------------------
False
trying possible lines: 2 [1, -1, -1, -1, 2, 2, -1, -1]
[[1, 0], [-1, 0], [2, 0], [2, 0], [-1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [1, 0], [-1, 0], [-1, 0], [-1, 0], [2, 0], [2, 0], [-1, 0]]
[[1, 3], [-1, 0], [-1, 0], [-1, 0], [2, 6], [2, 0], [-1, 0], [-1, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 6], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 6], [0

[[1, 0], [-1, 0], [2, 0], [2, 0], [-1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [-1, 0], [1, 0], [-1, 0], [-1, 0], [-1, 0], [2, 0], [2, 0]]
[[0, 3], [0, 0], [0, 0], [0, 0], [0, 6], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 6], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 6], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 6], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0]]

trying possible lines: 1 [-1, -1, -1, 1, -1, 2, 2, -1]
[[1, 0], [-1, 0], [2, 0], [2, 0], [-1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [-1, 0], [-1, 0], [1, 0], [-1, 0], [2, 0], [2, 0], [-1, 0]]
[[0, 3], [0, 0], [0, 0], [0, 0], [0, 6], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 6], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 6], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 6], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0

[[0, 0], [0, 0], [0, 0], [0, 0], [0, 6], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 6], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 6], [0, 0], [0, 0], [0, 0]]
before throw back
[[1, 0], [-1, 0], [-1, 0], [2, 0], [2, 0], [-1, 0], [-1, 0], [-1, 0]]
[[1, 0], [-1, 0], [-1, 0], [-1, 0], [2, 0], [2, 0], [-1, 0], [-1, 0]]
[[1, 3], [-1, 0], [-1, 0], [-1, 0], [2, 6], [2, 0], [-1, 0], [-1, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 6], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 6], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 6], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0]]


all trys in line 2 failed
[[1, 0], [-1, 0], [-1, 0], [2, 0], [2, 0], [-1, 0], [-1, 0], [-1, 0]]
[[1, 0], [-1, 0], [-1, 0

...

trying possible lines: 3 [-1, -1, -1, 2, 2, -1, -1, -1]
[[1, 0], [-1, 0], [-1, 0], [-1, 0], [-1, 0], [-1, 0], [2, 0], [2, 0]]
[[1, 0], [-1, 0], [2, 0], [2, 0], [-1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[1, 3], [-1, 0], [-1, 0], [-1, 0], [2, 6], [2, 0], [-1, 0], [-1, 0]]
[[-1, 0], [-1, 0], [-1, 0], [2, 0], [2, 6], [-1, 0], [-1, 0], [-1, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 6], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 6], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0]]
------------------------------
False
trying possible lines: 3 [-1, -1, -1, -1, 2, 2, -1, -1]
[[1, 0], [-1, 0], [-1, 0], [-1, 0], [-1, 0], [-1, 0], [2, 0], [2, 0]]
[[1, 0], [-1, 0], [2, 0], [2, 0], [-1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[1, 3], [-1, 0], [-1, 0], [-1, 0], [2, 6], [2, 0], [-1, 0], [-1, 0]]
[[-1, 0], [-1, 0], [-1, 0], [-1, 0], [2, 6], [2, 0], [-1, 0], [-1, 0]]
[[0, 0], [0, 0], [0, 0], [0, 

[[-1, 0], [-1, 0], [3, 0], [3, 0], [3, 6], [-1, 0], [-1, 0], [-1, 0]]
[[2, 0], [2, 0], [-1, 0], [-1, 0], [1, 6], [-1, 0], [-1, 0], [-1, 0]]
[[2, 0], [2, 0], [-1, 0], [-1, 0], [1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[1, 0], [-1, 0], [1, 0], [-1, 0], [-1, 0], [-1, 0], [-1, 0], [-1, 0]]
------------------------------
False
trying possible lines: 7 [1, -1, -1, 1, -1, -1, -1, -1]
[[1, 0], [-1, 0], [-1, 0], [-1, 0], [-1, 0], [-1, 0], [2, 0], [2, 0]]
[[1, 0], [-1, 0], [-1, 0], [-1, 0], [2, 0], [2, 0], [-1, 0], [-1, 0]]
[[1, 3], [-1, 0], [-1, 0], [-1, 0], [2, 6], [2, 0], [-1, 0], [-1, 0]]
[[-1, 0], [-1, 0], [-1, 0], [2, 0], [2, 6], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [-1, 0], [3, 0], [3, 0], [3, 6], [-1, 0], [-1, 0], [-1, 0]]
[[2, 0], [2, 0], [-1, 0], [-1, 0], [1, 6], [-1, 0], [-1, 0], [-1, 0]]
[[2, 0], [2, 0], [-1, 0], [-1, 0], [1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[1, 0], [-1, 0], [-1, 0], [1, 0], [-1, 0], [-1, 0], [-1, 0], [-1, 0]]
------------------------------
False
trying possible lines: 7 [1

trying possible lines: 7 [-1, 1, -1, -1, -1, 1, -1, -1]
[[1, 0], [-1, 0], [-1, 0], [-1, 0], [-1, 0], [-1, 0], [2, 0], [2, 0]]
[[1, 0], [-1, 0], [-1, 0], [-1, 0], [2, 0], [2, 0], [-1, 0], [-1, 0]]
[[1, 3], [-1, 0], [-1, 0], [-1, 0], [2, 6], [2, 0], [-1, 0], [-1, 0]]
[[-1, 0], [-1, 0], [-1, 0], [2, 0], [2, 6], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [-1, 0], [3, 0], [3, 0], [3, 6], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [2, 0], [2, 0], [-1, 0], [1, 6], [-1, 0], [-1, 0], [-1, 0]]
[[2, 0], [2, 0], [-1, 0], [-1, 0], [1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [1, 0], [-1, 0], [-1, 0], [-1, 0], [1, 0], [-1, 0], [-1, 0]]
------------------------------
False
trying possible lines: 7 [-1, 1, -1, -1, -1, -1, 1, -1]
[[1, 0], [-1, 0], [-1, 0], [-1, 0], [-1, 0], [-1, 0], [2, 0], [2, 0]]
[[1, 0], [-1, 0], [-1, 0], [-1, 0], [2, 0], [2, 0], [-1, 0], [-1, 0]]
[[1, 3], [-1, 0], [-1, 0], [-1, 0], [2, 6], [2, 0], [-1, 0], [-1, 0]]
[[-1, 0], [-1, 0], [-1, 0], [2, 0], [2, 6], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0]

[[0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0]]


all trys in line 2 failed
[[1, 0], [-1, 0], [-1, 0], [-1, 0], [-1, 0], [-1, 0], [2, 0], [2, 0]]
[[1, 0], [-1, 0], [-1, 0], [-1, 0], [2, 0], [2, 0], [-1, 0], [-1, 0]]
[[1, 3], [-1, 0], [-1, 0], [-1, 0], [2, 6], [2, 0], [-1, 0], [-1, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 6], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 6], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 6], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0], [0, 0]]
[[0, 3], [0, 0], [0, 0], [0, 0], [0, 6], [0, 0], [0, 0], [0, 0]]
before throw back
[[1, 0], [-1, 0], [-1, 0], [-1, 0], [-1, 0], [-1, 0], [2, 0], [2, 0]]
[[1, 0], [-1, 0], [-1, 0], [-1, 0], [2, 0], [2, 0], [-1, 0], [-1, 0]]
[[0, 3], [0, 0], [0, 0], [0, 0], [0, 6], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0, 0], [0, 0], [0, 6], [0, 0], [0, 0], [0, 0]]
[[0, 0], [0, 0], [0

[[2, 0], [2, 0], [-1, 0], [-1, 0], [1, 6], [-1, 0], [-1, 0], [-1, 0]]
[[2, 0], [2, 0], [-1, 0], [-1, 0], [1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [-1, 0], [1, 0], [-1, 0], [-1, 0], [-1, 0], [1, 0], [-1, 0]]
------------------------------
False
trying possible lines: 7 [-1, -1, 1, -1, -1, -1, -1, 1]
[[1, 0], [-1, 0], [-1, 0], [-1, 0], [-1, 0], [-1, 0], [2, 0], [2, 0]]
[[1, 0], [-1, 0], [-1, 0], [-1, 0], [-1, 0], [2, 0], [2, 0], [-1, 0]]
[[1, 3], [-1, 0], [-1, 0], [-1, 0], [2, 6], [2, 0], [-1, 0], [-1, 0]]
[[-1, 0], [-1, 0], [-1, 0], [2, 0], [2, 6], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [-1, 0], [3, 0], [3, 0], [3, 6], [-1, 0], [-1, 0], [-1, 0]]
[[2, 0], [2, 0], [-1, 0], [-1, 0], [1, 6], [-1, 0], [-1, 0], [-1, 0]]
[[2, 0], [2, 0], [-1, 0], [-1, 0], [1, 0], [-1, 0], [-1, 0], [-1, 0]]
[[-1, 0], [-1, 0], [1, 0], [-1, 0], [-1, 0], [-1, 0], [-1, 0], [1, 0]]
------------------------------
False
trying possible lines: 7 [-1, -1, -1, 1, -1, 1, -1, -1]
[[1, 0], [-1, 0], [-1, 0], [-1, 0], [-1, 

In [8]:
# %timeit solve(ls_h,ls_v) # took too long the run